# 라이브러리 설치, 모델 다운로드

In [ ]:
!pip install numpy insightface pillow opencv-python matplotlib

In [ ]:
#!pip install ort-nightly-gpu --index-url=https://aiinfra.pkgs.visualstudio.com/PublicPackages/_packaging/ort-cuda-12-nightly/pypi/simple/ #코랩 또는 cuda 12
!pip install onnxruntime #cpu 사용
#!pip install onnxruntime-gpu --extra-index-url https://aiinfra.pkgs.visualstudio.com/PublicPackages/_packaging/onnxruntime-cuda-12/pypi/simple/ # cuda12
#!pip install onnxruntime-gpu #cuda 12 미만

In [ ]:
!wget https://huggingface.co/ezioruan/inswapper_128.onnx/resolve/main/inswapper_128.onnx?download=true -O inswapper_128.onnx

# 파이썬 코드

In [9]:
from PIL import Image
import cv2
import matplotlib.pyplot as plt
from insightface.app import FaceAnalysis
import insightface

app = FaceAnalysis(allowed_modules=['detection','recognition'], providers=['CPUExecutionProvider', 'CUDAExecutionProvider'])
app.prepare(ctx_id=0, det_thresh=0.5, det_size=(640, 640))

swapper = insightface.model_zoo.get_model('inswapper_128.onnx',providers=['CPUExecutionProvider', 'CUDAExecutionProvider'])

Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
model ignore: /root/.insightface/models/buffalo_l/1k3d68.onnx landmark_3d_68
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
model ignore: /root/.insightface/models/buffalo_l/2d106det.onnx landmark_2d_106
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
find model: /root/.insightface/models/buffalo_l/det_10g.onnx detection [1, 3, '?', '?'] 127.5 128.0
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
model ignore: /root/.insightface/models/buffalo_l/genderage.onnx genderage
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
find model: /root/.insightface/models/buffalo_l/w600k_r50.onnx recognition ['None', 3, 112, 112] 127.5 127.5
set det-size: (640, 640)
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
inswap

In [10]:
img1 = cv2.imread('설국열차.jpg')
faces1 = app.get(img1)

img2 = cv2.imread('오징어게임2.webp')
faces2 = app.get(img2)

## 얼굴 탐지 시각화

In [11]:
def faceplot(img, faces):
    l = len(faces)
    x = l//5+1
    fig,axes=plt.subplots(nrows=x,ncols=5,figsize=(10,x*2))

    if x==1:
        for col in range(5):
            ax=axes[col]
            if col < l:
                box = faces[col].bbox
                roi = img[int(box[1]):int(box[3]), int(box[0]):int(box[2])]
                roi = cv2.cvtColor(roi,cv2.COLOR_BGR2RGB)
                ax.imshow(roi)
                ax.set_xlabel(str(col),fontsize=20)
            else:
                fig.delaxes(ax)
    else:
        for row in range(x):
            for col in range(5):
                idx = row*5+col
                ax=axes[row][col]
                if idx < l:
                    box = faces[idx].bbox
                    roi = img[int(box[1]):int(box[3]), int(box[0]):int(box[2])]
                    roi = cv2.cvtColor(roi,cv2.COLOR_BGR2RGB)
                    ax.imshow(roi)
                    ax.set_xlabel(str(idx),fontsize=20)
                else:
                    fig.delaxes(ax)
    plt.tight_layout()
    plt.show()

In [ ]:
faceplot(img1,faces1)

In [ ]:
faceplot(img2,faces2)

## 얼굴 바꾸기

In [ ]:
result = swapper.get(img2, faces2[6], faces1[2], paste_back=True)

temp = cv2.cvtColor(result, cv2.COLOR_BGR2RGB)
rimg = Image.fromarray(temp)
display(rimg)

In [15]:
def faceswap(img,faces1,faces2,l):
    for t in l:
        img = swapper.get(img, faces1[t[0]], faces2[t[1]], paste_back=True)

    temp = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    rimg = Image.fromarray(temp)
    display(rimg)

In [ ]:
faceswap(img2,faces2,faces1,[(6,2),(0,2),(4,1),(5,1),(1,0),(2,0),(3,0),(7,0)])

## 임베딩벡터 만들어 합성하기

In [17]:
import numpy as np
from insightface.app.common import Face

vector = np.random.normal(loc=0.0, scale=1.0, size=512).astype(np.float32)

base_face = faces1[0].copy()
random_face = Face(**base_face)
random_face.embedding = vector

In [ ]:
result = swapper.get(img2, faces2[1], random_face, paste_back=True)

temp = cv2.cvtColor(result, cv2.COLOR_BGR2RGB)
rimg = Image.fromarray(temp)
display(rimg)